<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#Web-Scraping" data-toc-modified-id="Web-Scraping-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>Web Scraping</a></span><ul class="toc-item"><li><span><a href="#Importación-de-librerías" data-toc-modified-id="Importación-de-librerías-1.1"><span class="toc-item-num">1.1&nbsp;&nbsp;</span>Importación de librerías</a></span></li><li><span><a href="#Definición-de-funciones" data-toc-modified-id="Definición-de-funciones-1.2"><span class="toc-item-num">1.2&nbsp;&nbsp;</span>Definición de funciones</a></span><ul class="toc-item"><li><span><a href="#HTML-parser" data-toc-modified-id="HTML-parser-1.2.1"><span class="toc-item-num">1.2.1&nbsp;&nbsp;</span>HTML parser</a></span></li><li><span><a href="#Directory-switcher" data-toc-modified-id="Directory-switcher-1.2.2"><span class="toc-item-num">1.2.2&nbsp;&nbsp;</span>Directory switcher</a></span></li><li><span><a href="#Image-downloader" data-toc-modified-id="Image-downloader-1.2.3"><span class="toc-item-num">1.2.3&nbsp;&nbsp;</span>Image downloader</a></span></li><li><span><a href="#Pager" data-toc-modified-id="Pager-1.2.4"><span class="toc-item-num">1.2.4&nbsp;&nbsp;</span>Pager</a></span></li></ul></li><li><span><a href="#Obtención-de-imágenes" data-toc-modified-id="Obtención-de-imágenes-1.3"><span class="toc-item-num">1.3&nbsp;&nbsp;</span>Obtención de imágenes</a></span><ul class="toc-item"><li><span><a href="#Mushroom-World" data-toc-modified-id="Mushroom-World-1.3.1"><span class="toc-item-num">1.3.1&nbsp;&nbsp;</span>Mushroom World</a></span></li><li><span><a href="#Wild-UK-Mushrooms" data-toc-modified-id="Wild-UK-Mushrooms-1.3.2"><span class="toc-item-num">1.3.2&nbsp;&nbsp;</span>Wild UK Mushrooms</a></span></li><li><span><a href="#Fungipedia" data-toc-modified-id="Fungipedia-1.3.3"><span class="toc-item-num">1.3.3&nbsp;&nbsp;</span>Fungipedia</a></span></li></ul></li></ul></li></ul></div>

# Web Scraping

La primera parte del proyecto consiste en la obtención, mediantes técnicas de Web Scraping, de:

*   Un set de imágenes de setas para entrenar un modelo Deep Learning  de clasificación multiclase.
*   Un dataset con los datos asociados a distintas especies de setas, para entrenar un modelo Machine Learning de clasificación multiclase. 

Toda la información será obtenida de las siguientes páginas web:


*   https://www.mushroom.world/
*   https://www.wildfooduk.com/mushroom-guide/
*   https://www.fungipedia.org/hongos/




## Importación de librerías 

In [1]:
# Importamos librerías
import requests                      # Librería HTTP
from bs4 import BeautifulSoup        # Extraer datos de archivos HTML y XML
import re                            # Regular Expressions
import os                            # Paths y directorios
import pathlib                       # Paths y directorios
import pandas as pd                  # Tratamiento de DataFrames
import numpy as np                   # Funciones matemáticas, algebraicas y otras
from PIL import Image                # Edición de imágenes
from resizeimage import resizeimage  # Reescalado de imágenes

## Definición de funciones

Para este ejercicio, definiremos una serie de funciones que nos facilitarán la ejecución y la estructura del mismo:

### HTML parser


Definimos en primer lugar una función general para ***parsear* la información de la URL facilitada**: 

In [2]:
def getdata(url, parser='html.parser'):
    #Definimos los headers para la request HTTP de manera que el servidor no nos bloquee la respuesta:
    headers = {
    'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/96.0.4664.110 Safari/537.36',
    'Accept-Language': 'es-ES,es;q=0.9', 
    'Cache-Control': 'max-age=0',
    'Referer': 'https://google.com',
    'DNT': '1',
    }
    dir = url
    r = requests.get(dir, headers = headers)
    soup = BeautifulSoup(r.text, parser)
    return soup

###  Directory switcher

Creamos también una función para crear y cambiar directorios en la carpeta raíz para nuestras imágenes:

In [3]:
directory = os.getcwd()
image_directory = os.path.join(directory + '\Images')
try:
    os.mkdir(image_directory)
except FileExistsError:
        pass

In [4]:
def getdirectory(folder):
    os.chdir(image_directory)
    try:
        os.mkdir(os.getcwd() + "/" + str(folder))
    except FileExistsError:
        pass
    os.chdir(os.getcwd() + "/" + str(folder))

### Image downloader

La siguientes funciones sirven para **descargar todas las imágenes de las distintas webs** anteriormente mencionadas:

1. La **primera función de descarga** es para https://www.mushroom.world/.

    En ella, usamos las *RE* para obtener los atributos "href" de cada imagen y obtener sus URLs. En este caso, todas son de la forma: *https://www.mushroom.world/data/...*. Después, iteraremos sobre este listado y escribiremos cada imagen en el directorio.

In [5]:
def imagedown_1(soup):
    images = soup.find_all(href=re.compile("data"))
    for image in images:
        href = image['href']
        link = 'https://www.mushroom.world' + image['href'][3:]
        name = href[15:-4] + ' mw' + '.jpg'
        name = name.replace('/','-')
        if not os.path.exists('./' + name): # Solo descargamos aquellas imágenes que no tengamos
            with open(name, 'wb') as f:
                im = requests.get(link)
                f.write(im.content)
            # Reescalamos la imagen a 512x512 píxeles
            with open(name, 'r+b') as f:
                try:
                    with Image.open(f) as image:
                        cover = resizeimage.resize_cover(image, [512, 512])
                        cover.save(name, image.format)
                except:
                    pass

2. Creamos ahora una **función para aplicar en la segunda web** utilizada : https://www.wildfooduk.com/mushroom-guide/

    En este caso, hacemos uso de las utilidades de BS4 y html para obtener las imágenes de cada página. Eso si, previamente necesitaremos un listado con todos los links individuales.

In [6]:
def imagedown_2(soup):
    image_set = soup.find('ul', {'class': 'mush-thumbs'})
    images = image_set.find_all('a', {'id': re.compile("image-")})
    contador = 0
    for image in images:
        contador += 1
        link = image['href']
        name = soup.find('table').find_all('td')[5].string.strip() + " " + str(contador) + ' wf' + '.jpg'
        name = name.replace('/','-')
        if not os.path.exists('./' + name): # Solo descargamos aquellas imágenes que no tengamos
            with open(name, 'wb') as f:
                im = requests.get(link)
                f.write(im.content)
            # Reescalamos la imagen a 512x512 píxeles
            with open(name, 'r+b') as f:
                try:
                    with Image.open(f) as image:
                        cover = resizeimage.resize_cover(image, [512, 512])
                        cover.save(name, image.format)
                except:
                    pass


3. Creamos ahora una función para aplicar en la **tercera y última web utilizada**: https://www.fungipedia.org/hongos.html

    En este caso utilizaremos CSS Selectors para obtener las imágenes, pues las imágenes se encuentran dentro de un plugin "Simple Image Gallery Pro". Al igual que en caso anterior, previamente necesitaremos un listado con todos los links individuales:

In [7]:
def imagedown_3(soup):
    # Utilizamos nuevamente headers, de lo contrario el servidor nos devuelve un codigo 403 Forbidden error.
    headers = {
        'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/96.0.4664.110 Safari/537.36',
        'Accept-Language': 'es-ES,es;q=0.9', 
        'Cache-Control': 'max-age=0',
        'Referer': 'https://google.com',
        'DNT': '1',
    }
    images = soup.select('.sigProLinkWrapper a[href]:not([href=""])')
    domain = 'https://www.fungipedia.org'
    contador = 0
    for image in images:
        contador += 1
        link = image.attrs.get('href')
        name = soup.find('h1', {'class': 'itemTitle'}).string.strip() + " " + str(contador) + ' fp' + '.jpg'
        name = name.replace('/','-')
        if not os.path.exists('./' + name): # Solo descargamos aquellas imágenes que no tengamos
            with open(name, 'wb') as f: 
                im = requests.get(domain + link, allow_redirects = True, headers = headers)
                f.write(im.content)
            # Reescalamos la imagen a 512x512 píxeles
            with open(name, 'r+b') as f:
                try:
                    with Image.open(f) as image:
                        cover = resizeimage.resize_cover(image, [512, 512])
                        cover.save(name, image.format)
                except:
                    pass

### Pager

En último lugar, definimos las funciones para **pasar de página** en las distintas estructuras de las webs:

1. Para https://www.mushroom.world:

In [8]:
def getnextpage_1(soup):
    page = soup.find('div', {'id': 'pager'})                    # A partir de la etiqueta de división div del paginador (id=pager), podemos pasar de página iterando en un bucle:
    if page.find(string=re.compile("Next Page")):
        url = 'https://www.mushroom.world' +  str(page.find('a', string=re.compile("Next Page"))['href'])
        return url
    else:
        return

2. Para https://www.wildfooduk.com/mushroom-guide/: en este caso encontramos todos los links en una única URL, luego no hará falta.

3. Para https://www.fungipedia.org/':

In [9]:
def getnextpage_2(soup):
    pager = soup.find('div', {'class': 'pagination'})
    if pager.find('a', {'class': 'next'}):
        url = 'https://www.fungipedia.org/' + str(pager.find('a', {'class': 'next'})['href'])
        return url
    else:
        return

## Obtención de imágenes

### Mushroom World 

Las distintas URLs del siguiente diccionario hacen referencia a las clases en las que dividiremos las imágenes de las setas:

*   **Edible** *(Comestibles)*
*   **Inedible** *(No Comestibles)*
*   **Poisonous** *(Venenosas)*

Cada una de ellas se guardará en una carpeta en nuestro directorio.

In [10]:
edibility = {"Edible"  :  'https://www.mushroom.world/mushrooms/edible', 
             "Inedible":  'https://www.mushroom.world/mushrooms/inedible', 
             "Poisonous": 'https://www.mushroom.world/mushrooms/poisonous'}

Con las funciones anteriormente definidas, simplemente planteamos el siguiente bucle para descargar todas las imágenes:

In [11]:
for i in edibility:
    url = edibility[i]
    getdirectory(i)
    while type(url) == str:
        soup  = getdata(url,'html.parser')
        imagedown_1(soup)
        url = getnextpage_1(soup)

### Wild UK Mushrooms

Fijamos las URLs nuevamente:

In [12]:
edibility = {"Edible"  :  'https://www.wildfooduk.com/mushroom-guide/?mushroom_type=edible', 
             "Inedible":  'https://www.wildfooduk.com/mushroom-guide/?mushroom_type=inedible', 
             "Poisonous": 'https://www.wildfooduk.com/mushroom-guide/?mushroom_type=poisonous'} 

Planteamos el bucle para recorrer la estructura de la web y descargar las imágenes:

In [13]:
for i in edibility:
    url = edibility[i]
    getdirectory(i)
    soup  = getdata(url)
    mushroom_table = soup.find_all('td', {'class': 'mushroom-image'})
    mushroom_links = []
    for mushroom in mushroom_table:
        mushroom_links.append(mushroom.find('a')['href'])
    for link in mushroom_links:
        soup  = getdata(link,'html.parser')
        imagedown_2(soup)

### Fungipedia 

Fijamos las URLs nuevamente, en este caso al aplicando los filtros correspondientes en la web, estos se reflejan directamente en las URLs.

In [14]:
edibility = {"Edible"  :  'https://www.fungipedia.org/hongos/itemlist/filter.html?array12%5B%5D=buen-comestible&array12%5B%5D=buen-comestible-precaucion&array12%5B%5D=comestible&array12%5B%5D=comestible-precaucion&array12%5B%5D=excelente-comestible&array12%5B%5D=excelente-comestible-precaucion&moduleId=95&Itemid=337', 
             "Inedible":  'https://www.fungipedia.org/hongos/itemlist/filter.html?array12%5B%5D=no-comestible&array12%5B%5D=sin-valor&moduleId=95&Itemid=337', 
             "Poisonous": 'https://www.fungipedia.org/hongos/itemlist/filter.html?array12%5B%5D=mortal&array12%5B%5D=toxica&moduleId=95&Itemid=337'} 

Planteamos el bucle para recorrer la estructura de la web y descargar las imágenes:

In [15]:
for i in edibility:
    url_main = edibility[i]
    getdirectory(i)
    while True:
        soup_main = getdata(url_main,'html.parser')
        mushroom_elements = soup_main.find_all('a', {'class': 'gris'})
        mushroom_links = []
        for element in mushroom_elements:
            mushroom_links.append('https://www.fungipedia.org' + element['href'])
        for link in mushroom_links:
            soup_link  = getdata(link,'html.parser')
            imagedown_3(soup_link)
        url_main = getnextpage_2(soup_main)
        if not url_main:
            break